In [1]:
from datasets import load_dataset

dataset = load_dataset("databricks/databricks-dolly-15k")

print(dataset)

dataset["train"].select(range(3))


README.md: 0.00B [00:00, ?B/s]

databricks-dolly-15k.jsonl:   0%|          | 0.00/13.1M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/15011 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['instruction', 'context', 'response', 'category'],
        num_rows: 15011
    })
})


Dataset({
    features: ['instruction', 'context', 'response', 'category'],
    num_rows: 3
})

In [2]:
from datasets import DatasetDict
import re

# rules: (pattern, new_category)
CATEGORY_RULES = [
    (r"\b(write|compose|generate).*email\b", "writing"),
    (r"\bsummarize|summary|brief\b", "summarization"),
    (r"\btranslate|translation\b", "translation"),
    (r"\bmath|calculate|equation\b", "math"),
    (r"\bclassify|classification\b", "classification"),
    (r"\bcode|python|function|script\b", "coding"),
    (r"\bdebug|fix.*code\b", "debugging"),
    (r"\bcompare|difference between\b", "comparison"),
    (r"\bquestion|quiz|ask\b", "question_answering"),
]

# Function to apply rules
def enrich_category(example):
    text = f"{example['instruction']} {example.get('context', '')}".lower()

    for pattern, cat in CATEGORY_RULES:
        if re.search(pattern, text):
            example["category_enriched"] = cat
            return example

    # fallback to existing category or "unknown"
    example["category_enriched"] = example.get("category") or "unknown"
    return example

# Apply enrichment
enriched_dataset = dataset["train"].map(enrich_category, desc="Enriching categories")

# Quick sanity check
enriched_dataset.select(range(5))


Enriching categories:   0%|          | 0/15011 [00:00<?, ? examples/s]

Dataset({
    features: ['instruction', 'context', 'response', 'category', 'category_enriched'],
    num_rows: 5
})

In [12]:
from sentence_transformers import SentenceTransformer
import numpy as np

# Light weight embedding model
model = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [13]:
from datasets import Dataset
import numpy as np

# concatenate fields and encode
def embed_row(row):

    text = f"{row['instruction']} {row['context']} {row['response']}".strip()


    embedding = model.encode(text, normalize_embeddings=True).tolist()


    return {"embedding": embedding}

# Apply with map (non-batched due to Hugging Face token handling)
enriched_dataset = enriched_dataset.map(embed_row)


Map:   0%|          | 0/15011 [00:00<?, ? examples/s]

In [19]:
sample = enriched_dataset[0]

print("Keys:", sample.keys())
print("First 5 dims of embedding:", sample["embedding"][:5])
print("Total dims:", len(sample["embedding"]))

Keys: dict_keys(['instruction', 'context', 'response', 'category', 'category_enriched', 'embedding'])
First 5 dims of embedding: [0.08877551555633545, -0.05551433563232422, 0.016190456226468086, 0.049700941890478134, -0.02064383588731289]
Total dims: 384


In [21]:
for i in range(5):
    print(f"Row {i}: {enriched_dataset['category_enriched']}")

Row 0: Column(['closed_qa', 'classification', 'open_qa', 'open_qa', 'closed_qa'])
Row 1: Column(['closed_qa', 'classification', 'open_qa', 'open_qa', 'closed_qa'])
Row 2: Column(['closed_qa', 'classification', 'open_qa', 'open_qa', 'closed_qa'])
Row 3: Column(['closed_qa', 'classification', 'open_qa', 'open_qa', 'closed_qa'])
Row 4: Column(['closed_qa', 'classification', 'open_qa', 'open_qa', 'closed_qa'])


In [22]:
from collections import Counter

# Flatten enriched labels
def compare_categories(example):
    return {
        "category_match": example["category"] in example["category_enriched"]
    }

# Apply comparison logic
comparison_results = enriched_dataset.map(compare_categories)

# Count mismatches
mismatch_count = Counter([r["category_match"] for r in comparison_results])
print(f"Match vs Mismatch:\n{mismatch_count}")


Map:   0%|          | 0/15011 [00:00<?, ? examples/s]

Match vs Mismatch:
Counter({True: 14050, False: 961})


In [25]:
import textstat
import tiktoken

encoding = tiktoken.get_encoding("cl100k_base")

def compute_complexity(example):
    instruction = example["instruction"]
    response = example["response"]

    return {
        "instruction_readability": textstat.flesch_kincaid_grade(instruction),
        "response_readability": textstat.flesch_kincaid_grade(response),
        "instruction_tokens": len(encoding.encode(instruction)),
        "response_tokens": len(encoding.encode(response)),
    }

# Apply complexity computation
enriched_dataset = enriched_dataset.map(compute_complexity)


Map:   0%|          | 0/15011 [00:00<?, ? examples/s]

In [26]:
for i in range(5):
    print(f"Row {i}")
    print("Instruction:", enriched_dataset[i]['instruction'])
    print("Instruction Readability:", enriched_dataset[i]['instruction_readability'])
    print("Instruction Tokens:", enriched_dataset[i]['instruction_tokens'])

    print("Response:", enriched_dataset[i]['response'])
    print("Response Readability:", enriched_dataset[i]['response_readability'])
    print("Response Tokens:", enriched_dataset[i]['response_tokens'])
    print("-" * 50)

Row 0
Instruction: When did Virgin Australia start operating?
Instruction Readability: 10.350000000000001
Instruction Tokens: 7
Response: Virgin Australia commenced services on 31 August 2000 as Virgin Blue, with two aircraft on a single route.
Response Readability: 9.785555555555558
Response Tokens: 23
--------------------------------------------------
Row 1
Instruction: Which is a species of fish? Tope or Rope
Instruction Readability: -0.7238888888888866
Instruction Tokens: 11
Response: Tope
Response Readability: -3.3999999999999986
Response Tokens: 2
--------------------------------------------------
Row 2
Instruction: Why can camels survive for long without water?
Instruction Readability: 5.230000000000004
Instruction Tokens: 10
Response: Camels use the fat in their humps to keep them filled with energy and hydration for long periods of time.
Response Readability: 8.140000000000004
Response Tokens: 23
--------------------------------------------------
Row 3
Instruction: Alice's par